In [1]:
import pandas
import os
import json
import pydantic
import glob

In [2]:
EXTRACTED_GAMES_PATH = os.path.join(os.getcwd(), 'extracted_games')
MAPPING_GAMES_PATH = os.path.join(os.getcwd(), 'mapping_data')
brackets = ['game-changers', 'vct-challengers', 'vct-international']
years = ['2022', '2023', '2024']

In [3]:
all_games = []
all_mapping = {}
all_players_mapping = {}
leagues_mapping = {}
teams_mapping = {}
tournaments_mapping = {}
for bracket in brackets:
    with open(os.path.join(MAPPING_GAMES_PATH, bracket, 'mapping_data.json'), 'r') as f:
        all_mapping[bracket]=json.load(f)

    with open(os.path.join(MAPPING_GAMES_PATH, bracket, 'players.json'), 'r') as p:
        all_players_mapping[bracket]=json.load(p)

    with open(os.path.join(MAPPING_GAMES_PATH, bracket, 'leagues.json'), 'r') as l:
        leagues_mapping[bracket]=json.load(l)

    with open(os.path.join(MAPPING_GAMES_PATH, bracket, 'teams.json'), 'r') as t:
        teams_mapping[bracket]=json.load(t)

    with open(os.path.join(MAPPING_GAMES_PATH, bracket, 'tournaments.json'), 'r') as tn:
        tournaments_mapping[bracket]=json.load(tn)

    for year in years:
        games = glob.glob(os.path.join(EXTRACTED_GAMES_PATH, bracket, year, '*.json'))
        for g in games:
            with open(g, 'r') as f:
                all_games.append(json.load(f))

        



In [4]:
def get_mapping_from_game(game, mapping):
    for k in mapping:
        for m in mapping[k]:
            if m['platformGameId'] == f'val:{game['id']}':
                return m
    print('couldnt find game')
    return None

In [5]:
# per player processing
# per game per player
# per player per round
#Are they a feast or famine player? (std deviation of kills per round) (easy)
#Which agents do they play? Statistics per agent (easy)
#Which roles do they play (sentinel, duelist, etc.)? Use agents to answer this (easy)
#Per map winrates (easy)
#Player-to-player matchup winrates (easy)
#X-factors (1v1+ winrates, multikills, first bloods) (medium)
#-> per player per round
#Weapon distribution? (easy)
#Ability usage? (easy)
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import pandas as pd
import numpy as np

In [6]:
all_mapping_df = pd.DataFrame(all_mapping.values())
all_players_mapping_df = pd.DataFrame(all_players_mapping.values())
leagues_mapping_df = pd.DataFrame(leagues_mapping.values())
teams_mapping_df = pd.DataFrame(teams_mapping.values())
tournaments_mapping_df = pd.DataFrame(tournaments_mapping.values())


In [7]:
print(teams_mapping)

{'game-changers': [{'id': '111006711389612074', 'acronym': 'LH', 'home_league_id': '109029777807406730', 'dark_logo_url': 'http://static.lolesports.com/teams/1693827991731_Lunatic-hailogo.png', 'light_logo_url': 'http://static.lolesports.com/teams/1693827991730_Lunatic-hailogo.png', 'slug': 'lunatichai-flax', 'name': 'Lunatic-hai flax'}, {'id': '109029888698112406', 'acronym': 'LWE', 'home_league_id': '109029777807406730', 'dark_logo_url': 'http://static.lolesports.com/teams/1663664070075_LWEwhite.png', 'light_logo_url': 'http://static.lolesports.com/teams/1663664070073_LWEwhite.png', 'slug': 'lone-way-esports', 'name': 'Lone Way E-SPORTS'}, {'id': '112439820691490172', 'acronym': 'MIR', 'home_league_id': '109029777807406730', 'dark_logo_url': 'http://static.lolesports.com/teams/1721811528651_Mir_Logo.png', 'light_logo_url': 'http://static.lolesports.com/teams/1721811528651_Mir_Logo.png', 'slug': 'mir-gaming', 'name': 'MIR Gaming'}, {'id': '112439825505751243', 'acronym': 'STG', 'home_

In [8]:
pandas.set_option("future.no_silent_downcasting", True)

In [41]:
all_games_and_players_df = None
all_games_and_teams_df = None
pd.set_option("future.no_silent_downcasting", True)
for g in all_games:
    mapping = get_mapping_from_game(g, all_mapping)
    
    #print(mapping)
    # pid gameid -> stats for a single game
    # pid stats -> stats for all games
    teams_normalized = pd.json_normalize(
    g['teams'], 
    'players', 
    ['id', 'side'], 
    record_prefix='player_'
    )

    # Rename some columns to match the SQL-like query format
    teams_normalized.rename(
        columns={'id': 'team_id', 'side': 'team_side'}, 
        inplace=True
    )

    # Add wins and losses columns based on the game winner
    teams_normalized['wins'] = teams_normalized['team_side'].apply(lambda x: 1 if x == g['winner'] else 0)
    teams_normalized['loss'] = 1 - teams_normalized['wins']

    # Select relevant columns for querying
    teams_df = teams_normalized[[
        'player_id', 'team_id', 'wins', 'loss', 'player_agent', 'player_kills', 'player_deaths', 
        'player_assists', 'player_first_bloods', 'player_first_deaths', 'player_clutches', 
        'player_combat_score', 'player_rounds'
    ]]

    # takes the dataframe and replaces the player id with the id from the mapping data
    # filters out the '-' instances which are null instances of the player 
    #print(teams_df)
    teams_df['player_id'].replace({int(k): v for k,v in mapping['participantMapping'].items()}, inplace=True)
    teams_df.loc[:, 'player_id'] = teams_df.loc[teams_df['player_id'] != '-']
    teams_df.loc[:, 'player_id'] = teams_df['player_id'].fillna(-1).astype(int)    
    teams_df['team_id'].replace({int(k): v for k,v in mapping['teamMapping'].items()}, inplace=True)
    teams_df = teams_df.loc[teams_df['team_id'] != '-']
    teams_df.loc[:, 'team_id'] = teams_df['team_id'].fillna(-1).astype(int)
    all_games_and_players_df = pd.concat([all_games_and_players_df, teams_df], ignore_index=True)

/tmp/ipykernel_210623/3034861208.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  teams_df['player_id'].replace({int(k): v for k,v in mapping['participantMapping'].items()}, inplace=True)
/tmp/ipykernel_210623/3034861208.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  teams_df['team_id'].replace({int(k): v for k,v in mapping['teamMapping'].items()}, inplace=True)
/tmp/ipykernel_210623/3034861208.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a

In [44]:
from collections import Counter
def aggregate_player_data(df):
    aggregated_data = []
    
    for player_id, group in df.groupby('player_id'):
        # Sum columns
        wins = group['wins'].sum()
        losses = group['loss'].sum()
        kills = group['player_kills'].sum()
        deaths = group['player_deaths'].sum()
        assists = group['player_assists'].sum()
        first_bloods = group['player_first_bloods'].sum()
        first_deaths = group['player_first_deaths'].sum()
        clutches = group['player_clutches'].sum()
        combat_score = group['player_combat_score'].sum()
        
        # Top 3 agents
        agent_counter = Counter(group['player_agent'])
        top_3_agents = tuple([agent for agent, _ in agent_counter.most_common(3)])
        
        # Extract 'primary' from player_rounds
        all_primaries = []
        for rounds in group['player_rounds']:
            all_primaries.extend([round_info['primary'] for round_info in rounds])
        
        # Top 2 primary weapons
        primary_counter = Counter(all_primaries)
        top_2_primaries = [primary for primary, _ in primary_counter.most_common(2)]
        
        # Append aggregated data
        aggregated_data.append({
            'player_id': player_id,
            'team_id': group['team_id'].iloc[0],
            'wins': wins,
            'loss': losses,
            'player_kills': kills,
            'player_deaths': deaths,
            'player_assists': assists,
            'player_first_bloods': first_bloods,
            'player_first_deaths': first_deaths,
            'player_clutches': clutches,
            'player_combat_score': combat_score,
            'top_3_agents': top_3_agents,
            'top_2_primaries': top_2_primaries
        })
    
    return pd.DataFrame(aggregated_data)
gg = aggregate_player_data(all_games_and_players_df)
print(gg)

               player_id             team_id  wins  loss  player_kills  \
0                     -1  110768163318645416    10    23           353   
1      99566407765334300  105665869861005803    57    45          1363   
2     103537287230111095  105680972836508184    95    41          1553   
3     106116425673582104  109637705013640848    32    25           873   
4     106116439896241774  108844205153870167    32    34           908   
...                  ...                 ...   ...   ...           ...   
2153  112829096887354461  111006703702614704     0     2            23   
2154  112829098135710904  111006703702614704     0     1             9   
2155  112829099617017574  111006703702614704     0     3            52   
2156  112840152290521871  112127272470502649     0     5            47   
2157  112891299631595293  107910153514729818     5     1           130   

      player_deaths  player_assists  player_first_bloods  player_first_deaths  \
0               489           